In [1]:
import numpy as np 
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import plotly.express as px

import plotly.io as pio
pio.renderers.default = "browser"

# pd.set_option("display.max_rows", None)
# pd.set_option("display.max_columns", None)
# pd.set_option("display.width", None)
# pd.set_option("display.max_colwidth", None)

## Population

In [46]:
dwell_file_names = ["2000-2010.csv", "2011-2020.csv", "2021.csv", "2022.csv", "2023.csv", "2024.csv", "2025.csv"]

total_dwell_df = pd.DataFrame()
for dwell_file_name in dwell_file_names:
    dwell_df = pd.read_pickle(f'./data/dwell_population/{dwell_file_name.replace(".csv", ".pkl")}')
    total_dwell_df = pd.concat([total_dwell_df, dwell_df], ignore_index=True)

total_dwell_df["SC_pop_int"] = (
    total_dwell_df["Pop"]
      .astype(str)
      .str.strip()
      .str.replace(",", "", regex=False)
      .pipe(pd.to_numeric, errors="coerce")
      .astype("Int64")
)

total_dwell_1_6_df = total_dwell_df[total_dwell_df["Age"].isin([str(i) for i in range(1, 7)])]

combine_sex_age_df = (
    total_dwell_1_6_df.groupby(["PA", "SZ", "Time"], as_index=False)["SC_pop_int"].sum()
)

In [47]:
sc_perc = 1
combine_sex_age_df["Pop"] = combine_sex_age_df["SC_pop_int"] / sc_perc

In [48]:
combine_sex_age_df.head()

PA                      SZ  Time  SC_pop_int    Pop
0  Ang Mo Kio  Ang Mo Kio Town Centre  2011         360  360.0
1  Ang Mo Kio  Ang Mo Kio Town Centre  2012         340  340.0
2  Ang Mo Kio  Ang Mo Kio Town Centre  2013         320  320.0
3  Ang Mo Kio  Ang Mo Kio Town Centre  2014         330  330.0
4  Ang Mo Kio  Ang Mo Kio Town Centre  2015         360  360.0

In [5]:
def dynamic_rolling_cagr_forecast(g, window=5, horizon=5, cagr_cap=0.20, pop_floor=0):
    g = g.sort_values("Time").copy()

    for _ in range(horizon):
        lag = g["Pop"].shift(window)

        # rolling CAGR with protection against 0/negative/NA lag
        cagr = np.where(
            (lag.isna()) | (lag <= 0) | (g["Pop"] < 0),
            np.nan,
            (g["Pop"] / lag) ** (1 / window) - 1
        )
        g["rolling_cagr"] = cagr

        last = g.iloc[-1]
        cagr_last = last["rolling_cagr"]

        # stop if CAGR not computable or not finite
        if pd.isna(cagr_last) or not np.isfinite(cagr_last):
            break

        # cap extreme CAGR to avoid blow-ups
        cagr_last = float(np.clip(cagr_last, -cagr_cap, cagr_cap))

        next_time = int(last["Time"] + 1)
        next_pop = last["Pop"] * (1 + cagr_last)

        # safety: enforce finite + floor
        if not np.isfinite(next_pop):
            break

        next_pop = int(round(max(pop_floor, next_pop)))

        g = pd.concat([
            g,
            pd.DataFrame({
                "PA": [last["PA"]],
                "SZ": [last["SZ"]],
                "Time": [next_time],
                "Pop": [next_pop]
            })
        ], ignore_index=True)

    return g

In [6]:
forecast_df = (
    combine_sex_age_df.groupby(["PA", "SZ"], group_keys=False).apply(dynamic_rolling_cagr_forecast, window=5, horizon=5, cagr_cap=0.20)
)

forecast_2026_2030_df = forecast_df[
    (forecast_df["Time"] >= 2026) & (forecast_df["Time"] <= 2030)
]

forecast_2026_2030_df.head()

C:\Users\Lim Family\AppData\Local\Temp\ipykernel_9552\2990107008.py:2: FutureWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



PA                      SZ  Time  SC_pop_int    Pop  rolling_cagr
15  Ang Mo Kio  Ang Mo Kio Town Centre  2026        <NA>  139.0     -0.095815
16  Ang Mo Kio  Ang Mo Kio Town Centre  2027        <NA>  126.0     -0.128061
17  Ang Mo Kio  Ang Mo Kio Town Centre  2028        <NA>  110.0     -0.121312
18  Ang Mo Kio  Ang Mo Kio Town Centre  2029        <NA>   97.0     -0.116310
19  Ang Mo Kio  Ang Mo Kio Town Centre  2030        <NA>   86.0           NaN

In [7]:
# combine_sex_age_df[combine_sex_age_df["SZ"] == "Tampines North"]

### Backtesting

In [9]:
df = combine_sex_age_df.sort_values(["SZ", "Time"])

In [10]:
def rolling_cagr_forecast(series, window):
    start = series.iloc[-window]
    end = series.iloc[-1]
    if start <= 0:
        return np.nan
    cagr = (end / start) ** (1 / window) - 1
    return end * (1 + cagr)

def backtest_window_with_preds(df, window_years):
    records = []

    for sz, g in df.groupby("SZ"):
        g = g.sort_values("Time")

        for i in range(len(g) - 1):
            end_year = g.iloc[i]["Time"]
            start_year = end_year - window_years

            # find the row corresponding to start_year
            start_row = g[g["Time"] == start_year]

            if start_row.empty:
                continue

            start_pop = start_row["Pop"].values[0]
            end_pop = g.iloc[i]["Pop"]

            if start_pop <= 0:
                continue

            # CAGR using actual year difference
            cagr = (end_pop / start_pop) ** (1 / window_years) - 1

            actual = g.iloc[i + 1]["Pop"]
            pred = end_pop * (1 + cagr)

            records.append({
                "SZ": sz,
                "train_start_year": start_year,
                "train_end_year": end_year,
                "forecast_year": g.iloc[i + 1]["Time"],
                "window": window_years,
                "cagr": cagr,
                "cagr_pct": cagr * 100,
                "actual": actual,
                "predicted": pred,
                "abs_error": abs(pred - actual),
                "pct_error": abs(pred - actual) / actual if actual > 0 else None
            })

    return pd.DataFrame(records)

all_preds = []

for w in [2, 3, 4, 5]:
    all_preds.append(backtest_window_with_preds(df, w))

pred_df = pd.concat(all_preds, ignore_index=True)

In [11]:
def backtest_fixed_cagr_with_preds(df, window_years, horizon=5, cagr_cap=None, dup_agg="mean"):
    records = []

    for sz, g in df.groupby("SZ"):
        g = g.sort_values("Time").copy()

        # 1) Ensure ONE value per year (handles duplicates)
        if dup_agg == "mean":
            pop_by_year = g.groupby("Time")["Pop"].mean()
        elif dup_agg == "max":
            pop_by_year = g.groupby("Time")["Pop"].max()
        elif dup_agg == "last":
            pop_by_year = g.drop_duplicates("Time", keep="last").set_index("Time")["Pop"]
        else:
            raise ValueError("dup_agg must be one of: 'mean', 'max', 'last'")

        years = sorted(pop_by_year.index.astype(int).tolist())
        years_set = set(years)

        for T in years:
            start_year = T - window_years
            if start_year not in years_set:
                continue

            future_years = [T + h for h in range(1, horizon + 1)]
            if not all(y in years_set for y in future_years):
                continue

            # 2) Scalar extraction guaranteed now
            start_pop = float(pop_by_year.loc[start_year])
            end_pop = float(pop_by_year.loc[T])

            if start_pop <= 0:
                continue

            cagr = (end_pop / start_pop) ** (1 / window_years) - 1
            if cagr_cap is not None:
                cagr = float(np.clip(cagr, -cagr_cap, cagr_cap))

            pred = end_pop
            for h in range(1, horizon + 1):
                pred = pred * (1 + cagr)
                y = T + h
                actual = float(pop_by_year.loc[y])

                records.append({
                    "SZ": sz,
                    "origin_year": T,
                    "train_start_year": start_year,
                    "train_end_year": T,
                    "forecast_year": y,
                    "horizon": h,
                    "window": window_years,
                    "cagr": cagr,
                    "cagr_pct": cagr * 100,
                    "actual": actual,
                    "predicted": pred,
                    "abs_error": abs(pred - actual),
                    "pct_error": abs(pred - actual) / actual if actual > 0 else None
                })

    return pd.DataFrame(records)

all_fixed = []
for w in [2, 3, 4, 5]:
    all_fixed.append(backtest_fixed_cagr_with_preds(df, window_years=w, horizon=5, cagr_cap=0.20))

pred_fixed_df = pd.concat(all_fixed, ignore_index=True)

In [12]:
window_perf = (
    pred_df
    .groupby("window")
    .agg(
        mape=("pct_error", "mean"),
        mae=("abs_error", "mean"),
        rmse=("abs_error", lambda x: (x**2).mean() ** 0.5),
        n_obs=("pct_error", "count")
    )
    .reset_index()
)

window_perf["mape_pct"] = window_perf["mape"] * 100
window_perf.sort_values("mape_pct")

window      mape         mae        rmse  n_obs   mape_pct
3       5  0.144802  109.434190  457.130799   3813  14.480185
2       4  0.145177  110.228761  471.611940   4062  14.517681
1       3  0.148165  115.653196  520.065555   4304  14.816542
0       2  0.165387  126.276561  641.858183   4546  16.538672

In [13]:
window_perf = (
    pred_fixed_df
    .groupby("window")
    .agg(
        mape=("pct_error", "mean"),
        mae=("abs_error", "mean"),
        rmse=("abs_error", lambda x: (x**2).mean() ** 0.5),
        n_obs=("pct_error", "count")
    )
    .reset_index()
)

window_perf["mape_pct"] = window_perf["mape"] * 100
window_perf.sort_values("mape_pct")

window      mape         mae        rmse  n_obs   mape_pct
2       4  0.222243  181.333214  525.098254  15516  22.224341
3       5  0.224162  184.575601  545.479165  14366  22.416214
1       3  0.224493  177.931143  498.531856  16673  22.449325
0       2  0.233655  176.681024  474.712305  17840  23.365488

## Preschools

In [14]:
preschools_gdf = gpd.read_file("./data/preschool_location/location.geojson") # Last Updated: Jun 2024
subzones_gdf = gpd.read_file("./data/subzone_boundary/boundary.geojson") # Last Updated: Dec 25

In [15]:
preschools_with_sz_df = gpd.sjoin(
    preschools_gdf,
    subzones_gdf[["SUBZONE_N", "PLN_AREA_N", "REGION_N", "geometry"]],
    how="left",
    predicate="within"
)

In [16]:
preschool_counts = (
    preschools_with_sz_df
    .groupby(["SUBZONE_N", "PLN_AREA_N", "REGION_N"])
    .size()
    .reset_index(name="num_preschools")
)

In [17]:
subzones_proj = subzones_gdf.to_crs(epsg=3414)
subzones_proj["area_km2"] = subzones_proj.geometry.area / 1_000_000

subzone_area = subzones_proj[[
    "SUBZONE_N", "PLN_AREA_N", "REGION_N", "area_km2"
]]

density_df = preschool_counts.merge(
    subzone_area,
    on=["SUBZONE_N", "PLN_AREA_N", "REGION_N"],
    how="left"
)

density_df["num_preschools_per_km2"] = (
    density_df["num_preschools"] / density_df["area_km2"]
)

density_df["supply"] = (
    density_df["num_preschools"] * 100
)

density_df["supply_per_km2"] = (
    density_df["supply"] / density_df["area_km2"]
)

density_df = density_df.sort_values(
    by="supply_per_km2",
    ascending=False
)

density_df.head(10)

SUBZONE_N     PLN_AREA_N           REGION_N  num_preschools  \
31                  CECIL  DOWNTOWN CORE     CENTRAL REGION               7   
117         MANDAI ESTATE         MANDAI       NORTH REGION               5   
164     SEMBAWANG CENTRAL      SEMBAWANG       NORTH REGION              27   
151               PHILLIP  DOWNTOWN CORE     CENTRAL REGION               1   
176       SERANGOON NORTH      SERANGOON  NORTH-EAST REGION              17   
170  SENGKANG TOWN CENTRE       SENGKANG  NORTH-EAST REGION              33   
215        WOODLANDS EAST      WOODLANDS       NORTH REGION              54   
94                 KATONG  MARINE PARADE     CENTRAL REGION              22   
126               MIDVIEW      WOODLANDS       NORTH REGION              19   
95              KEAT HONG  CHOA CHU KANG        WEST REGION              23   

     area_km2  num_preschools_per_km2  supply  supply_per_km2  
31   0.196620               35.601693     700     3560.169296  
117  0.143138               34.931339     500     3493.133940  
164  0.961422               28.083410    2700     2808.340956  
151  0.039438               25.356297     100     2535.629701  
176  0.684704               24.828236    1700     2482.823605  
170  1.460534               22.594469    3300     2259.446890  
215  2.553464               21.147745    5400     2114.774512  
94   1.078992               20.389400    2200     2038.940000  
126  0.936416               20.290138    1900     2029.013773  
95   1.143814               20.108170    2300     2010.817016

In [18]:
# density_df[density_df["SUBZONE_N"] == "Tampines North".upper()]

### Visualization

In [19]:
map_gdf = subzones_gdf.merge(
    density_df,
    on="SUBZONE_N",
    how="left"
)

map_gdf = map_gdf.to_crs(epsg=4326)

geojson = map_gdf.__geo_interface__

fig = px.choropleth_map(
    map_gdf,
    geojson=geojson,
    locations=map_gdf.index,
    color="supply_per_km2",
    color_continuous_scale="YlOrRd",
    map_style="carto-positron",
    zoom=10.5,
    center={"lat": 1.35, "lon": 103.82},
    opacity=0.8,
    hover_data={
        "SUBZONE_N": True,
        "PLN_AREA_N_x": True,
        "REGION_N_x": True,
        "num_preschools": True,
        "supply": True,
        "supply_per_km2": ":,.0f"
    },
    title="Preschool Supply Density by Subzone (places per km²)"
)

fig.update_layout(margin={"r":0,"t":40,"l":0,"b":0})
fig.show()

## Combine

In [19]:
density_df["SUBZONE_N_clean"] = density_df["SUBZONE_N"].str.strip().str.upper()
density_df["PLN_AREA_N_clean"] = density_df["PLN_AREA_N"].str.strip().str.upper()

forecast_2026_2030_df["SZ_clean"] = forecast_2026_2030_df["SZ"].str.strip().str.upper()
forecast_2026_2030_df["PA_clean"] = forecast_2026_2030_df["PA"].str.strip().str.upper()

merged_df = forecast_2026_2030_df.merge(
    density_df[["PLN_AREA_N_clean", "SUBZONE_N_clean", "supply", "supply_per_km2", "num_preschools"]],
    left_on=["PA_clean", "SZ_clean"],
    right_on=["PLN_AREA_N_clean", "SUBZONE_N_clean"],
    how="left"
)

C:\Users\Lim Family\AppData\Local\Temp\ipykernel_9552\755901185.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\Lim Family\AppData\Local\Temp\ipykernel_9552\755901185.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [20]:
take_up_rate = 0.9
merged_df["trend_demand"] = merged_df["Pop"] * take_up_rate

In [21]:
merged_df.head()

PA                      SZ  Time  SC_pop_int    Pop  rolling_cagr  \
0  Ang Mo Kio  Ang Mo Kio Town Centre  2026        <NA>  139.0     -0.095815   
1  Ang Mo Kio  Ang Mo Kio Town Centre  2027        <NA>  126.0     -0.128061   
2  Ang Mo Kio  Ang Mo Kio Town Centre  2028        <NA>  110.0     -0.121312   
3  Ang Mo Kio  Ang Mo Kio Town Centre  2029        <NA>   97.0     -0.116310   
4  Ang Mo Kio  Ang Mo Kio Town Centre  2030        <NA>   86.0           NaN   

                 SZ_clean    PA_clean PLN_AREA_N_clean  \
0  ANG MO KIO TOWN CENTRE  ANG MO KIO       ANG MO KIO   
1  ANG MO KIO TOWN CENTRE  ANG MO KIO       ANG MO KIO   
2  ANG MO KIO TOWN CENTRE  ANG MO KIO       ANG MO KIO   
3  ANG MO KIO TOWN CENTRE  ANG MO KIO       ANG MO KIO   
4  ANG MO KIO TOWN CENTRE  ANG MO KIO       ANG MO KIO   

          SUBZONE_N_clean  supply  supply_per_km2  num_preschools  \
0  ANG MO KIO TOWN CENTRE   400.0     1262.299463             4.0   
1  ANG MO KIO TOWN CENTRE   400.0     1262.299463             4.0   
2  ANG MO KIO TOWN CENTRE   400.0     1262.299463             4.0   
3  ANG MO KIO TOWN CENTRE   400.0     1262.299463             4.0   
4  ANG MO KIO TOWN CENTRE   400.0     1262.299463             4.0   

   trend_demand  
0         125.1  
1         113.4  
2          99.0  
3          87.3  
4          77.4

In [22]:
# merged_df[merged_df["SZ"] == "Yishun West"]

### BTO

In [50]:
bto_df = pd.read_pickle("./data/bto/bto.pkl")
bto_df.head()

bto_df["Estimated completion year"] = pd.to_numeric(
    bto_df["Estimated completion year"], errors="coerce"
)
bto_df["Total number of units"] = pd.to_numeric(
    bto_df["Total number of units"], errors="coerce"
)

bto_26_30 = bto_df[
    (bto_df["Estimated completion year"] >= 2026) &
    (bto_df["Estimated completion year"] <= 2030)
].copy()

annual_units = (
    bto_26_30
    .groupby(["Planning area", "Subzone", "Estimated completion year"], as_index=False)
    .agg(units=("Total number of units", "sum"))
)

subzones = annual_units["Subzone"].unique()
planning_areas = annual_units["Planning area"].unique()
years = list(range(2026, 2031))

full_index = pd.MultiIndex.from_product(
    [planning_areas, subzones, years],
    names=["Planning area", "Subzone", "Year"]
)

annual_units_full = (
    annual_units
    .set_index(["Planning area", "Subzone", "Estimated completion year"])
    .reindex(full_index, fill_value=0)
    .reset_index()
    .rename(columns={"level_1": "Year"})
)

annual_units_full["cum_units_from_2026"] = (
    annual_units_full
    .groupby("Subzone")["units"]
    .cumsum()
)

total_fertility_rate = 0.97 # each woman about 1 children
new_families_factor = 0.9 

annual_units_full["bto_demand"] = annual_units_full["cum_units_from_2026"]  * total_fertility_rate * new_families_factor * take_up_rate

annual_units_full["Subzone"] = annual_units_full["Subzone"].str.strip().str.upper()
annual_units_full["Planning area"] = annual_units_full["Planning area"].str.strip().str.upper()
# BTO demand is cumulative, unlikes population trend predictions. 

In [51]:
annual_units

Planning area                 Subzone  Estimated completion year  units
0     Ang Mo Kio  Ang Mo Kio Town Centre                       2028    896
1          Bedok             Bedok North                       2027    433
2          Bedok             Bedok South                       2027   2168
3          Bedok               Kembangan                       2027   1234
4         Bishan             Bishan East                       2026   1502
..           ...                     ...                        ...    ...
60     Woodlands          Woodlands West                       2028    399
61        Yishun                  Khatib                       2028   1277
62        Yishun           Lower Seletar                       2028    699
63        Yishun           Lower Seletar                       2029   2295
64        Yishun          Yishun Central                       2026    646

[65 rows x 4 columns]

In [24]:
bto_merged_df = merged_df.merge(
    annual_units_full,
    left_on=["PA_clean", "SZ_clean", "Time"],
    right_on=["Planning area", "Subzone", "Year"],
    how="left"
)

bto_merged_df["bto_demand"] = bto_merged_df["bto_demand"].fillna(0)

In [40]:
# bto_merged_df[bto_merged_df["SZ"] == "Yishun West"]

In [26]:
bto_merged_df["total_demand"] = bto_merged_df["bto_demand"] + bto_merged_df["trend_demand"]
bto_merged_df["Supply_Demand_Gap"] = bto_merged_df["supply"] - bto_merged_df["total_demand"]

In [27]:
cleaned_df = bto_merged_df[["PA", "SZ", "Time", "trend_demand", "bto_demand", "total_demand", "supply", "Supply_Demand_Gap"]]

In [28]:
cleaned_df

PA                      SZ  Time  trend_demand  bto_demand  \
0     Ang Mo Kio  Ang Mo Kio Town Centre  2026         125.1      0.0000   
1     Ang Mo Kio  Ang Mo Kio Town Centre  2027         113.4      0.0000   
2     Ang Mo Kio  Ang Mo Kio Town Centre  2028          99.0    703.9872   
3     Ang Mo Kio  Ang Mo Kio Town Centre  2029          87.3    703.9872   
4     Ang Mo Kio  Ang Mo Kio Town Centre  2030          77.4    703.9872   
...          ...                     ...   ...           ...         ...   
1037      Yishun             Yishun West  2026        1356.3      0.0000   
1038      Yishun             Yishun West  2027        1264.5      0.0000   
1039      Yishun             Yishun West  2028        1176.3      0.0000   
1040      Yishun             Yishun West  2029        1090.8      0.0000   
1041      Yishun             Yishun West  2030        1009.8      0.0000   

      total_demand  supply  Supply_Demand_Gap  
0            125.1   400.0              274.9  
1            113.4   400.0              286.6  
2         802.9872   400.0          -402.9872  
3         791.2872   400.0          -391.2872  
4         781.3872   400.0          -381.3872  
...            ...     ...                ...  
1037        1356.3  2200.0              843.7  
1038        1264.5  2200.0              935.5  
1039        1176.3  2200.0             1023.7  
1040        1090.8  2200.0             1109.2  
1041        1009.8  2200.0             1190.2  

[1042 rows x 8 columns]

In [41]:
sz_summary = (
    cleaned_df
    .groupby(["PA", "SZ"])
    .agg(
        min_gap=("Supply_Demand_Gap", "min"),   # worst shortage
        max_gap=("Supply_Demand_Gap", "max"),   # biggest surplus
        avg_gap=("Supply_Demand_Gap", "mean"),
        years_short=("Supply_Demand_Gap", lambda x: (x < 0).sum()),
        years_surplus=("Supply_Demand_Gap", lambda x: (x > 0).sum())
    )
    .reset_index()
)

In [42]:
sz_summary

PA                      SZ   min_gap  max_gap    avg_gap  \
0    Ang Mo Kio  Ang Mo Kio Town Centre -402.9872    286.6 -122.83232   
1    Ang Mo Kio               Cheng San     412.5    607.8     513.66   
2    Ang Mo Kio              Chong Boon     269.1    417.6     347.22   
3    Ang Mo Kio             Kebun Bahru     330.3    459.0      393.3   
4    Ang Mo Kio         Sembawang Hills     130.0    134.5      132.7   
..          ...                     ...       ...      ...        ...   
207      Yishun              Springleaf      66.8     74.0      70.22   
208      Yishun          Yishun Central  -15.5622  -1.1622    -9.0822   
209      Yishun             Yishun East   -3012.1  -2831.2   -2930.02   
210      Yishun            Yishun South     530.5    851.8     691.24   
211      Yishun             Yishun West     843.7   1190.2    1020.46   

     years_short  years_surplus  
0            3.0            2.0  
1            0.0            5.0  
2            0.0            5.0  
3            0.0            5.0  
4            0.0            5.0  
..           ...            ...  
207          0.0            5.0  
208          5.0            0.0  
209          5.0            0.0  
210          0.0            5.0  
211          0.0            5.0  

[212 rows x 7 columns]

In [43]:
shortage_sz = sz_summary[sz_summary["years_short"] > 0].sort_values("avg_gap", ascending=True)
shortage_sz.head()

PA              SZ    min_gap    max_gap     avg_gap  \
178     Tampines  Tampines North   -12372.8    -5939.6    -8951.18   
21   Bukit Batok      Brickworks -4286.9464 -3488.9434  -3974.5852   
133      Punggol      Northshore    -5448.7    -2213.2    -3685.06   
179     Tampines   Tampines West -3395.4118 -2310.2341 -2951.39626   
209       Yishun     Yishun East    -3012.1    -2831.2    -2930.02   

     years_short  years_surplus  
178          5.0            0.0  
21           5.0            0.0  
133          5.0            0.0  
179          5.0            0.0  
209          5.0            0.0

In [44]:
surplus_sz = sz_summary[sz_summary["years_surplus"] > 0].sort_values("avg_gap", ascending=False)
surplus_sz.head()

PA             SZ    min_gap    max_gap     avg_gap  \
177       Tampines  Tampines East  1964.6181  2462.3181   2215.7181   
14           Bedok        Frankel     1917.9     2075.4     1995.48   
109  Marine Parade         Katong     1788.7     1857.1     1823.62   
58     Bukit Timah     Swiss Club     1538.2     1549.9     1543.42   
77         Geylang       Aljunied  1081.5349     1966.0  1422.22792   

     years_short  years_surplus  
177          0.0            5.0  
14           0.0            5.0  
109          0.0            5.0  
58           0.0            5.0  
77           0.0            5.0

### Visualization

In [33]:
subzones_gdf["SUBZONE_N"] = subzones_gdf["SUBZONE_N"].str.strip().str.upper()
sz_summary["SZ"] = sz_summary["SZ"].str.strip().str.upper()

map_gap_gdf = subzones_gdf.merge(
    sz_summary,
    left_on="SUBZONE_N",
    right_on="SZ",
    how="left"
)
map_gap_gdf["avg_gap"] = pd.to_numeric(map_gap_gdf["avg_gap"], errors="coerce")
map_gap_plot = map_gap_gdf.dropna(subset=["avg_gap"]).copy()
max_abs_gap = float(map_gap_plot["avg_gap"].max())
avg_abs_gap = float(map_gap_plot["avg_gap"].mean())
min_abs_gap = float(map_gap_plot["avg_gap"].min())


In [34]:
# symmetric range so 0 is exactly centered
max_abs = float(np.nanmax(np.abs(map_gap_plot["avg_gap"])))

# custom diverging colorscale with WHITE at 0
red_white_green = [
    [0.0, "rgb(165,0,38)"],   # red
    [0.5, "white"],           # 0 -> white
    [1.0, "rgb(0,104,55)"],   # green
]

geojson = map_gap_plot.__geo_interface__

fig = px.choropleth_map(
    map_gap_plot,
    geojson=geojson,
    locations=map_gap_plot.index,
    color="avg_gap",
    color_continuous_scale=red_white_green,
    range_color=[-max_abs, max_abs],     # <-- key for centering 0
    map_style="carto-positron",
    zoom=10.5,
    center={"lat": 1.35, "lon": 103.82},
    opacity=0.85,
    hover_data={
        "SUBZONE_N": True,
        "PLN_AREA_N": True,
        "REGION_N": True,
        "avg_gap": ":,.0f",
        "years_short": True,
        "years_surplus": True
    },
    title="Preschool Supply–Demand Gap by Subzone (2026–2030)"
)

fig.update_layout(
    width=1100,
    height=800,
    margin={"r":0,"t":60,"l":0,"b":0},
    coloraxis_colorbar=dict(title="Supply Surplus")
)

fig.show()

## Subzone Maturity

In [256]:
total_dwell_2025_df = total_dwell_df[total_dwell_df["Time"] == 2025].copy()

def age_to_numeric(x):
    if x == "90_and_Over":
        return 90
    return int(x)

total_dwell_2025_df["age_num"] = total_dwell_2025_df["Age"].apply(age_to_numeric)

age_pop = (
    total_dwell_2025_df
    .groupby(["PA", "SZ", "age_num"], as_index=False)
    .agg(pop=("Pop", "sum"))
)

# --- Weighted average age ---
def weighted_mean_age(g):
    denom = g["pop"].sum()
    if denom == 0:
        return np.nan
    return (g["age_num"] * g["pop"]).sum() / denom

avg_age_sz = (
    age_pop.groupby(["PA", "SZ"])
    .apply(weighted_mean_age)
    .reset_index(name="avg_age_2025")
    .dropna(subset=["avg_age_2025"])
)

# --- Weighted median age (NO row repetition) ---
def weighted_median_age(g):
    denom = g["pop"].sum()
    if denom == 0:
        return np.nan
    g = g.sort_values("age_num").copy()
    cum = g["pop"].cumsum()
    cutoff = denom / 2
    return int(g.loc[cum >= cutoff, "age_num"].iloc[0])

median_age_sz = (
    age_pop.groupby(["PA", "SZ"])
    .apply(weighted_median_age)
    .reset_index(name="median_age_2025")
)

age_summary = avg_age_sz.merge(median_age_sz, on=["PA", "SZ"], how="left")

C:\Users\Lim Family\AppData\Local\Temp\ipykernel_23816\576510607.py:25: FutureWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.

C:\Users\Lim Family\AppData\Local\Temp\ipykernel_23816\576510607.py:42: FutureWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



In [258]:
p33, p66 = age_summary["median_age_2025"].quantile([0.33, 0.66])

def bucket_maturity(age):
    if age < p33:
        return "Non-mature"
    elif age < p66:
        return "Mixed"
    else:
        return "Mature"

age_summary["maturity_bucket"] = age_summary["median_age_2025"].apply(bucket_maturity)

In [271]:
age_summary[age_summary["SZ"] == "Katong"]

PA      SZ  avg_age_2025  median_age_2025 maturity_bucket
116  Marine Parade  Katong      43.31134             44.0           Mixed